In [47]:
import time
import requests
from bs4 import BeautifulSoup
from random import randint
import logging
import json
import os
import dateparser

logging.basicConfig(level=logging.INFO)

headers = {
    "User-Agent": "Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/58.0.3029.110 Safari/537.3"
}


def fix_json_file(filename):
    with open(filename, "r+") as file:
        content = file.read()
        last_brace = content.rfind("}")
        file.seek(0)
        file.write(content[: last_brace + 1])
        file.write("]")
        file.truncate()


fix_json_file("jobs.json")


def scrape_linkedin_job(base_urls):
    with open("used_urls.json", "a+") as f:
        f.seek(0)
        used_urls = f.read().splitlines()

    jobs = load_jobs()
    job_codes = set(
        job["title"] + job["company"] + job["location"] for job in jobs
    )  # Create a set of all existing job links
    for base_url in base_urls:
        # Skip if URL has been used before
        """if base_url in used_urls:
            continue"""

        # Add URL to used URLs file
        with open("used_urls.json", "a") as f:
            f.write(base_url + "\n")

        for i in range(0, 975, 25):  # 25 * 40 = 1000
            url = f"{base_url}&start={i}"
            response = make_request(url)
            if response is not None:
                soup = BeautifulSoup(response.text, "html.parser")
                job_cards = soup.find_all("li")
                for job_card in job_cards:
                    job = {}
                    title_tag = job_card.find("h3", class_="base-search-card__title")
                    company_tag = job_card.find(
                        "h4", class_="base-search-card__subtitle"
                    )
                    location_tag = job_card.find(
                        "span", class_="job-search-card__location"
                    )
                    date_tag = job_card.find(
                        "time", class_="job-search-card__listdate--new"
                    )
                    if not date_tag:
                        date_tag = job_card.find(
                            "time", class_="job-search-card__listdate"
                        )

                    salary_tag = job_card.find(
                        "span", class_="job-search-card__salary-info"
                    )

                    link_tag = job_card.find("a", href=True)
                    if title_tag:
                        job["title"] = title_tag.text.strip()
                    if company_tag:
                        job["company"] = company_tag.text.strip()
                    if location_tag:
                        job["location"] = location_tag.text.strip()
                    if date_tag:
                        relative_date = date_tag.text.strip()
                        absolute_date = dateparser.parse(relative_date)
                        job["date"] = absolute_date.strftime("%Y-%m-%d %H:%M:%S")
                    if salary_tag:
                        job["salary"] = salary_tag.text.strip()
                    if link_tag:
                        job["link"] = link_tag["href"]
                    if (
                        job
                        and all(
                            key in job
                            for key in ("title", "company", "location", "link")
                        )
                        and job["title"] + job["company"] + job["location"]
                        not in job_codes
                    ):
                        jobs.append(job)
                        job_codes.add(
                            job["title"] + job["company"] + job["location"]
                        )  # Add the new link to the set of links

                logging.info(f"Page {i} scraped successfully")
                save_jobs(jobs)
    return jobs


def make_request(url, retries=2):
    for i in range(retries):
        try:
            time.sleep(randint(1, 5))  # Random sleep to avoid getting blocked
            response = requests.get(url, headers=headers)
            response.raise_for_status()  # If the response contains an HTTP error status code, raise an exception
            return response
        except requests.exceptions.HTTPError as errh:
            logging.error("HTTP Error:", errh)
        except requests.exceptions.ConnectionError as errc:
            logging.error("Error Connecting:", errc)
        except requests.exceptions.Timeout as errt:
            logging.error("Timeout Error:", errt)
        except requests.exceptions.RequestException as err:
            logging.error("Something Else:", err)
    return None


def save_jobs(jobs):
    with open("jobs.json", "w") as f:
        json.dump(jobs, f)


def load_jobs():
    if os.path.exists("jobs.json"):
        with open("jobs.json", "r") as f:
            return json.load(f)
    return []


def clean_jobs():
    jobs = load_jobs()

    # Keep track of unique jobs
    unique_jobs = []
    job_codes = set()

    for job in jobs:
        # Check if job has all required fields and is not a duplicate
        if (
            all(key in job for key in ("title", "company", "location", "link"))
            and job["title"] + job["company"] + job["location"] not in job_codes
        ):
            unique_jobs.append(job)
            job_codes.add(job["title"] + job["company"] + job["location"])

    save_jobs(unique_jobs)

    print(f"Cleaned jobs. {len(unique_jobs)} unique jobs remaining.")


base_urls = [
    "https://www.linkedin.com/jobs-guest/jobs/api/seeMoreJobPostings/search?keywords=undefined&location=United%2BStates&geoId=103644278&trk=public_jobs_jobs-search-bar_search-submit&pageNum=0",
    "https://www.linkedin.com/jobs-guest/jobs/api/seeMoreJobPostings/search?currentJobId=3634589578&f_I=6&geoId=103644278&keywords=project%20manager&location=United%20States&refresh=true&sortBy=R",
    "https://www.linkedin.com/jobs-guest/jobs/api/seeMoreJobPostings/search?keywords=Project%2BManager&location=United%2BStates&locationId=&geoId=103644278&f_TPR=&f_PP=102571732%2C102277331%2C103112676%2C104472865&start=25",
"https://www.linkedin.com/jobs-guest/jobs/api/seeMoreJobPostings/search?keywords=Product%2BManager&location=United%2BStates&locationId=&geoId=103644278&f_TPR=&f_PP=102571732&start=25",
"https://www.linkedin.com/jobs-guest/jobs/api/seeMoreJobPostings/search?keywords=Product%2BManager&location=United%2BStates&locationId=&geoId=103644278&f_TPR=&f_PP=103112676&start=25",
"https://www.linkedin.com/jobs-guest/jobs/api/seeMoreJobPostings/search?keywords=Product%2BManager&location=United%2BStates&locationId=&geoId=103644278&f_TPR=&f_PP=103112676&f_SB2=1&start=25",
"https://www.linkedin.com/jobs-guest/jobs/api/seeMoreJobPostings/search?keywords=Product%2BManager&location=United%2BStates&locationId=&geoId=103644278&f_TPR=&f_SB2=1&start=25",
"https://www.linkedin.com/jobs-guest/jobs/api/seeMoreJobPostings/search?keywords=Product%2BManager&location=United%2BStates&locationId=&geoId=103644278&f_TPR=&f_E=5&start=25",
"https://www.linkedin.com/jobs-guest/jobs/api/seeMoreJobPostings/search?keywords=Product%2BManager&location=United%2BStates&locationId=&geoId=103644278&f_TPR=&f_SB2=3&start=25",
"https://www.linkedin.com/jobs-guest/jobs/api/seeMoreJobPostings/search?keywords=Product%2BManager&location=United%2BStates&locationId=&geoId=103644278&f_TPR=&f_SB2=4&start=25",
"https://www.linkedin.com/jobs-guest/jobs/api/seeMoreJobPostings/search?keywords=Product%2BManager&location=United%2BStates&locationId=&geoId=103644278&f_TPR=&f_SB2=5&start=25",
"https://www.linkedin.com/jobs-guest/jobs/api/seeMoreJobPostings/search?keywords=Product%2BManager&location=United%2BStates&locationId=&geoId=103644278&f_TPR=&f_E=1&start=25",
"https://www.linkedin.com/jobs-guest/jobs/api/seeMoreJobPostings/search?keywords=Product%2BManager&location=United%2BStates&locationId=&geoId=103644278&f_TPR=&f_E=3&start=25",
"https://www.linkedin.com/jobs-guest/jobs/api/seeMoreJobPostings/search?keywords=Product%2BManager&location=United%2BStates&locationId=&geoId=103644278&f_TPR=&f_WT=1&start=25",
"https://www.linkedin.com/jobs-guest/jobs/api/seeMoreJobPostings/search?keywords=Product%2BManager&location=United%2BStates&locationId=&geoId=103644278&f_TPR=&f_WT=2&start=25",
    "https://www.linkedin.com/jobs-guest/jobs/api/seeMoreJobPostings/search?currentJobId=3657329295&f_I=50&geoId=103644278&keywords=project%20manager&location=United%20States&refresh=true&sortBy=R",
    "https://www.linkedin.com/jobs-guest/jobs/api/seeMoreJobPostings/search?currentJobId=3634589578&f_I=6&geoId=103644278&keywords=project%20manager&location=United%20States&refresh=true&sortBy=R",
    "https://www.linkedin.com/jobs-guest/jobs/api/seeMoreJobPostings/search?currentJobId=3643854088&f_I=104&geoId=103644278&keywords=project%20manager&location=United%20States&refresh=true&sortBy=R",
    "https://www.linkedin.com/jobs-guest/jobs/api/seeMoreJobPostings/search?currentJobId=3641288674&f_I=11&geoId=103644278&keywords=project%20manager&location=United%20States&refresh=true&sortBy=R",
    "https://www.linkedin.com/jobs-guest/jobs/api/seeMoreJobPostings/search?currentJobId=3511511926&f_I=44&geoId=103644278&keywords=project%20manager&location=United%20States&refresh=true&sortBy=R",
    "https://www.linkedin.com/jobs-guest/jobs/api/seeMoreJobPostings/search?currentJobId=3634589578&f_I=41%2C15%2C27&geoId=103644278&keywords=project%20manager&location=United%20States&refresh=true&sortBy=R",
    "https://www.linkedin.com/jobs-guest/jobs/api/seeMoreJobPostings/search?currentJobId=3619084191&f_I=96&geoId=103644278&keywords=project%20manager&location=United%20States&refresh=true&sortBy=R",
    "https://www.linkedin.com/jobs-guest/jobs/api/seeMoreJobPostings/search?currentJobId=3655917005&f_E=3%2C5%2C6&geoId=103644278&keywords=project%20manager&location=United%20States&refresh=true&sortBy=R",
    "https://www.linkedin.com/jobs-guest/jobs/api/seeMoreJobPostings/search?currentJobId=3653993392&f_E=4&f_WT=2&geoId=103644278&keywords=project%20manager&location=United%20States&refresh=true&sortBy=R",
    "https://www.linkedin.com/jobs-guest/jobs/api/seeMoreJobPostings/search?currentJobId=3641044468&f_I=15%2C112%2C19&geoId=103644278&keywords=project%20manager&location=United%20States&refresh=true&sortBy=R",
]
jobs = scrape_linkedin_job(base_urls)
print(len(jobs))



def scrape_job_details(job_link):
    try:
        response = make_request(job_link)
        if response is not None:
            soup = BeautifulSoup(response.text, "html.parser")

            job_details_div = soup.find(
                "div",
                {
                    "class": "show-more-less-html__markup show-more-less-html__markup--clamp-after-5 relative overflow-hidden"
                },
            )
            job_details = job_details_div.text if job_details_div else ""

            job_criteria_ul = soup.find(
                "ul", {"class": "description__job-criteria-list"}
            )
            job_criteria_items = (
                job_criteria_ul.find_all(
                    "li", {"class": "description__job-criteria-item"}
                )
                if job_criteria_ul
                else []
            )

            job_criteria = {}
            for item in job_criteria_items:
                key = item.find(
                    "h3", {"class": "description__job-criteria-subheader"}
                ).text
                value = item.find(
                    "span",
                    {
                        "class": "description__job-criteria-text description__job-criteria-text--criteria"
                    },
                ).text
                job_criteria[key.strip()] = value.strip()
            logging.info(f"Job details scraped successfully for {job_link}")
            return job_details, job_criteria
        logging.error(f"Error fetching details for {job_link}")
        return None, {}
    except Exception as e:
        logging.error(f"Error fetching details for {job_link}: {e}")
        return None, {}
    
    
be = 0
# In your main function, after you've scraped the job details, add this:
for job in jobs:
    if "details" in job.keys():
        logging.info(f"Skipping {job['link']} as it has already been scraped")
        continue
    job_details, job_criteria = scrape_job_details(job["link"])
    if job_details is not None:

        print(job_details[:50])
        be += 1
        print(be)
        job["details"] = job_details.strip()
        job.update(job_criteria)
    save_jobs(jobs)


INFO:root:Page 0 scraped successfully
INFO:root:Page 25 scraped successfully
INFO:root:Page 50 scraped successfully
INFO:root:Page 75 scraped successfully
INFO:root:Page 100 scraped successfully
INFO:root:Page 125 scraped successfully
INFO:root:Page 150 scraped successfully
INFO:root:Page 175 scraped successfully
INFO:root:Page 200 scraped successfully
INFO:root:Page 225 scraped successfully
INFO:root:Page 250 scraped successfully
INFO:root:Page 275 scraped successfully
INFO:root:Page 300 scraped successfully
INFO:root:Page 325 scraped successfully
INFO:root:Page 350 scraped successfully
INFO:root:Page 375 scraped successfully
INFO:root:Page 400 scraped successfully
INFO:root:Page 425 scraped successfully
INFO:root:Page 450 scraped successfully
INFO:root:Page 475 scraped successfully
INFO:root:Page 500 scraped successfully
INFO:root:Page 525 scraped successfully
INFO:root:Page 550 scraped successfully
--- Logging error ---
Traceback (most recent call last):
  File "C:\Users\tevfik.erku

11323


INFO:root:Skipping https://www.linkedin.com/jobs/view/graphic-designer-at-lockton-3656664709?refId=qtZKPNoPb%2F62KLWmn%2B2fVQ%3D%3D&trackingId=bcXJdt%2Bhcig%2F2yhH3SV%2BHw%3D%3D&position=25&pageNum=0&trk=public_jobs_jserp-result_search-card as it has already been scraped
INFO:root:Skipping https://www.linkedin.com/jobs/view/rn-clinical-ii-behavioral-health-per-diem-8-hour-shifts-at-kpc-health-3656660332?refId=vVQ0W4hhgS8Nbts0gF5rrQ%3D%3D&trackingId=vjra9GhAt3WLKYAwo5dLVg%3D%3D&position=1&pageNum=0&trk=public_jobs_jserp-result_search-card as it has already been scraped
INFO:root:Skipping https://www.linkedin.com/jobs/view/caregiver-at-comforcare-3655194772?refId=vVQ0W4hhgS8Nbts0gF5rrQ%3D%3D&trackingId=0NcrzBA0zeATc2q6rJ%2BSLQ%3D%3D&position=2&pageNum=0&trk=public_jobs_jserp-result_search-card as it has already been scraped
INFO:root:Skipping https://www.linkedin.com/jobs/view/registered-nurse-rn-icu-at-northwell-health-3656655090?refId=vVQ0W4hhgS8Nbts0gF5rrQ%3D%3D&trackingId=hKBxu7CaQeJ


        Performs routine maintenance and construc
1


INFO:root:Job details scraped successfully for https://www.linkedin.com/jobs/view/staff-assistant-iii-3812-at-nasa-jet-propulsion-laboratory-3655323021?refId=FdM6CBCAKnrThUV1SWG3hg%3D%3D&trackingId=aBrw0SJqRXA7iq3FFzcl7w%3D%3D&position=19&pageNum=0&trk=public_jobs_jserp-result_search-card


...

--- Logging error ---
Traceback (most recent call last):
  File "C:\Users\tevfik.erkut\AppData\Local\Temp\ipykernel_4088\2941055082.py", line 114, in make_request
    response.raise_for_status()  # If the response contains an HTTP error status code, raise an exception
  File "c:\Users\tevfik.erkut\Anaconda3\lib\site-packages\requests\models.py", line 1021, in raise_for_status
    raise HTTPError(http_error_msg, response=self)
requests.exceptions.HTTPError: 429 Client Error: Request denied for url: https://www.linkedin.com/jobs/view/project-manager-at-maronda-homes-3641203434?refId=PqB1vnrrEUN0tXR6GkZsXw%3D%3D&trackingId=mrtL5JYUOo5YMTq0hP%2BNfg%3D%3D&position=4&pageNum=16&trk=public_jobs_jserp-result_search-card

During handling of the above exception, another exception occurred:

Traceback (most recent call last):
  File "c:\Users\tevfik.erkut\Anaconda3\lib\logging\__init__.py", line 1083, in emit
    msg = self.format(record)
  File "c:\Users\tevfik.erkut\Anaconda3\lib\logging\__init


Multiple projects with a GC/CM based in Manhattan
7300


INFO:root:Job details scraped successfully for https://www.linkedin.com/jobs/view/project-manager-at-michael-page-3651768504?refId=PqB1vnrrEUN0tXR6GkZsXw%3D%3D&trackingId=l7JJllJV6%2FhPtf9tDUyWIA%3D%3D&position=6&pageNum=16&trk=public_jobs_jserp-result_search-card



Opportunities for Growth|Reputable Company About 
7301


KeyboardInterrupt: 

In [43]:
fix_json_file("jobs.json")

In [20]:
job

{'title': 'Senior Analyst, M&A',
 'company': 'The AES Corporation',
 'location': 'Salt Lake City, UT',
 'date': '2023-07-06 05:46:45',
 'link': 'https://www.linkedin.com/jobs/view/senior-analyst-m-a-at-the-aes-corporation-3655307973?refId=dqglD2ygFRMb59lpRgdP4A%3D%3D&trackingId=EFqzgHT0o7AO4jgc1cqseg%3D%3D&position=14&pageNum=0&trk=public_jobs_jserp-result_search-card'}